In [1]:
from tifffile import TiffFile

In [2]:
tif = TiffFile("AICS-11_2_4.ome.tif")

In [3]:
tif.ome_metadata

{'Experimenter': {'ID': 'Experimenter:0', 'UserName': 'derekt'},
 'Instrument': {'Microscope': {'Type': 'Inverted'},
  'Detector': {'ID': 'Detector:4.0', 'Model': 'HDCamC11440-22C'},
  'Objective': {'ID': 'Objective:1',
   'Immersion': 'Water',
   'LensNA': 1.25,
   'NominalMagnification': 100.0,
   'WorkingDistance': 260.0,
   'WorkingDistanceUnit': 'µm'},
  'ID': 'Instrument:0'},
 'Image': {'AcquisitionDate': '2016-07-05T22:52:04.774',
  'ExperimenterRef': {'ID': 'Experimenter:0'},
  'InstrumentRef': {'ID': 'Instrument:0'},
  'ObjectiveSettings': {'ID': 'Objective:1'},
  'Pixels': {'Channel': [{'DetectorSettings': {'Binning': '1x1',
      'ID': 'Detector:4.0'},
     'LightPath': None,
     'AcquisitionMode': 'SpinningDiskConfocal',
     'Color': -16771329,
     'EmissionWavelength': 683.0,
     'EmissionWavelengthUnit': 'nm',
     'ExcitationWavelength': 647.0,
     'ExcitationWavelengthUnit': 'nm',
     'Fluor': 'DRAQ5',
     'ID': 'Channel:0:0',
     'IlluminationType': 'Other',
  

In [4]:
img = tif.asarray()

In [5]:
names = [x['Name'] for x in tif.ome_metadata['Image']['Pixels']['Channel']]
xlabel = "x/"+tif.ome_metadata['Image']['Pixels']['PhysicalSizeXUnit']
ylabel = "y/"+tif.ome_metadata['Image']['Pixels']['PhysicalSizeYUnit']
zlabel = "z/"+tif.ome_metadata['Image']['Pixels']['PhysicalSizeZUnit']
xmaxextent = img.shape[3]*tif.ome_metadata['Image']['Pixels']['PhysicalSizeX']
ymaxextent = img.shape[2]*tif.ome_metadata['Image']['Pixels']['PhysicalSizeY']
zmaxextent = img.shape[0]*tif.ome_metadata['Image']['Pixels']['PhysicalSizeZ']

In [6]:
import matplotlib.pyplot as plt
import ipywidgets as ipw
%matplotlib inline

In [7]:
@ipw.interact(img_slice=(0,img.shape[0]), channel=names, 
              plane=['xy','yz','zx'], cmap=['gray', 'viridis'], 
              vscale=False)
def pltImg(img_slice,channel,plane, vscale, cmap):
    c=names.index(channel)
    plt.figure(0)
    if plane=='xy':
        i = min(img_slice,img.shape[0])
        im = img[i,c,...]
        yl = xlabel
        xl = ylabel
        xmax = xmaxextent
        ymax = ymaxextent
    elif plane=='yz':
        i = min(img_slice,img.shape[3])
        im = img[:,c,i,:]
        xl = ylabel
        yl = zlabel
        xmax = zmaxextent
        ymax = ymaxextent
    else:
        i = min(img_slice,img.shape[2])
        im = img[:,c,:,i]
        xl = zlabel
        yl = ylabel
        xmax = zmaxextent
        ymax = xmaxextent
    imargs = {"cmap": cmap,
              "extent":(0,xmax,0,ymax),
              "aspect":"equal",
             }
    if vscale:
        plt.imshow(im,vmin=np.min(img[:,c,:,:]), vmax=np.max(img[:,c,:,:]), **imargs)
    else:
        plt.imshow(im, **imargs)
    plt.xlabel(xl)
    plt.ylabel(yl)
    plt.show()

interactive(children=(IntSlider(value=24, description='img_slice', max=48), Dropdown(description='channel', op…